In [1]:
import os
import pickle
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
import numpy as np
import pandas as pd
from konlpy.tag import Okt
import random
import re

In [2]:
df = pd.read_csv('./travel_spot.csv', index_col=0)
df = df.fillna('')

In [3]:
df2 = pd.read_csv('./travel_spot.csv', index_col=0)
df2 = df2.fillna('')

In [4]:
df2['city'] = '전체'

In [5]:
joined_df = pd.concat([df,df2], axis=0, ignore_index=True)

In [6]:
len(df),len(df2),len(joined_df)

(10517, 10517, 21034)

In [91]:
joined_df['vec'] = joined_df['catchtitle'].apply(lambda x: x[:100]) + joined_df['treatMenu'].apply(lambda x: x[:200]) + joined_df['tagName'].apply(lambda x: x[:200]) + joined_df['overView'].apply(lambda x: x[:200])
joined_df['vec_f'] = joined_df['catchtitle'].apply(lambda x: x[:100]) + joined_df['treatMenu'].apply(lambda x: x[:200]) + joined_df['tagName'].apply(lambda x: x[:200])

In [92]:
spot_df = joined_df[joined_df['contentType'] != 39]
food_df = joined_df[joined_df['contentType'] == 39]
spot_df.__len__(), food_df.__len__()

(9268, 11766)

In [32]:
len(spot_df), len(food_df)

(9268, 11766)

In [10]:
okt = Okt()

In [33]:
spot_df[spot_df['city'] != '전체']['vec'].tolist()[0]

'숲과 문화가 어우러지는 서울의 대표적인 녹색쉼터가족여행,걷기길,관광지,데이트코스,반려동물동반여행지,생태관광지,서울숲,수도권,수도권반려동물여행지,아이와함께,연인과함께,연중무휴,피크닉,한국관광100선,휴식공간,휴식여행,휴식하기,휴식하기좋은곳2005년 6월 18일 ‘서울숲’ 개원 이전까지는 임금의 사냥터였고 1908년 설치된 서울 최초의 상수원 수원지였으며, 이후 경마장, 골프장으로 활용되기도 했다. 현재 ‘서울숲’은 18만 평 규모의 4개 테마공원으로서 환경친화적인 대규모 휴식 공간으로 탈바꿈하였다. 영국의 하이드파크(Hyde Park), 뉴욕의 센트럴파크(Central Park)와 같이 서'

In [12]:
spot_df['city'].unique()

array(['서울', '인천', '대전', '대구', '광주', '부산', '울산', '세종시', '경기', '강원', '충북',
       '충남', '경북', '경남', '전북', '전남', '제주', '전체'], dtype=object)

In [78]:
test = ['설치', '기도', '활용', '여행지', '환경', '파크', '최초', '영국', '아이', '뉴욕', '연중', '대표', '여행', '공간', '문화', '사냥터', '데이트', '이전', '경마장', '생태관광', '관광지', '휴식', '수원지', '연인', '상수', '대규모', '이드', '임금', '골프장', '서울숲', '서울', '녹색', '가족', '센트럴', '수도권', '피크닉', '관광', '이후', '테마', '현재', '코스', '규모', '한국', '반려동물', '공원', '개원', '탈바꿈']
len(test)

47

In [62]:

test.append(['a','b'])
test

['a', 'a', 'a', 'a', 'b', ['a', 'b'], ['a', 'b'], ['a', 'b']]

In [100]:
len(tag_list_all)

4634

In [167]:
# spot 학습

vectorizer_spot = TfidfVectorizer()
vectorizer_food = TfidfVectorizer()



# 전체 도시에 대한 TF-IDF 행렬 계산
tag_list_all = []
for i in spot_df[spot_df['city'] != '전체']['vec'].tolist():
    tag_list_all.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(len(tag_list_all))

matrix_spot = vectorizer_spot.fit_transform(tag_list_all)

# 각 도시에 대한 TF-IDF 행렬 계산
city_matrices_spot = {}
for city in spot_df['city'].unique():
    tag_list_city = []
    city_df = spot_df[spot_df['city'] == city]
    
    for i in city_df['vec'].tolist():
        tag_list_city.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        # print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        print(tag_list_city[-1][-5:-1])
        

    city_matrices_spot[city] = vectorizer_spot.transform(tag_list_city)


뉴욕 서울숲 골프장 연중 개원 규모 파크 활용 문화 대표 관광지 데이트 아이 영국 최초 가족 설치 수도권 임금 생태관광 센트럴 환경 경마장 이후 테마 코스 관광 공원 반려동물 서울 사냥터 녹색 연인 여행 휴식 이전 상수 현재 탈바꿈 대규모 공간 기도 여행지 한국 이드 피크닉 수원지
1
주인 당시 불교 김영한 연중 중턱 개원 도심 외국인 종교 상화 사찰 문화 관광지 길상사 원각 비롯 예전 수도권 대지 관광객 프로그램 자리 자연 시주 불도 수련 서울 역사 시가 성북동 여행 휴식 연속 전통 자연환경 건물 마련 체험 공간 산사 한국 위치
2
남대문시장 정책 홀로 거듭 쇼핑 중국 을사조약 풍전등화 도심 야간 나들이 혼미 광장시장 고종 시장 데이트 아이 국내 최초 가족 로서 나라 정세 수도권 상설 실질 경제 일본 맛집 침략 코스 관광 각축 행사 체결 종로 여행 연인 구한말 우리 장악 주권 전통 먹거리 강세 우리나라 국운 따라서 친구 돌파구 기도 투어 경영
3
왕실 성곽 본래 사산 청룡 낙타산 우유 체험학습 힐링 시민 산이 모습 나들이 야간 복원 문화 일대 낙산 중심 관광지 데이트 아이 해당 낙타 가족 아파트 야경 수도권 걷기 수립 보급 사업 타락 이후 코스 관광 공원 역사 서울 하나로 지형 진행 드라이브 여행 연인 일환 주택 목장 밀집 친구 서울시 계획
4
이성계 고궁 즉위 경희궁 유적지 규모 통역사 으뜸 문화 태조 사랑 관광지 아이 성종 궁궐 가족 북궐 정종 당일치기 다섯 수도권 이나 북쪽 교과서 자랑 투어 세종 근정전 코스 관광 서울 역사 경복궁 조선왕조 종로 여행 연인 인생 동궐 우리 법궁 가운데 세조 시절 불리 단종 체험 친구 창덕궁 기도 한국 위치 근교 건축
5
남녀 홀로 부근 쇼핑 체험학습 힐링 상품 장사 나들이 강원도 통해 경기도 형성 알리 이름 데이트 시장 아이 시작 가족 레이스 북부 수도권 청량리역 모두 등지 자리 자연 이후 맛집 개설 코스 판매 사람 서울 전쟁 한약재 열차 연인 여행 동시 회복 전통 공지 먹거리 노소 농산물 위해 반입 대규모 친구 재래시

In [168]:
# food 학습

# 전체 도시에 대한 TF-IDF 행렬 계산
tag_list_all_food = []
for i in food_df[food_df['city'] != '전체']['vec'].tolist():
    tag_list_all_food.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
    print(len(tag_list_all_food))


matrix_food = vectorizer_food.fit_transform(tag_list_all_food)

# 각 도시에 대한 TF-IDF 행렬 계산
city_matrices_food = {}
for city in food_df['city'].unique():
    tag_list_city_food = []
    city_df = food_df[food_df['city'] == city]
    
    for i in city_df['vec'].tolist():
        tag_list_city_food.append(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        # print(' '.join(list(set([j for j in okt.nouns(i) if len(j) > 1 and any(char.isalpha() and not char.isascii() for char in j)]))))
        print(tag_list_city_food[-1][-5:-1])
        
        
    city_matrices_food[city] = vectorizer_food.transform(tag_list_city_food)


꼬리 육수 중이 백련산 소면 설렁탕 불광천 새절역 깃밥 구이 고기 대표 신사동 출구 곰탕 황태 호선 사용 은평구 음식 운영 맛집 꼬리곰탕 이상 서울 메뉴인 시간 주문 돌판 전통 가로수길 도가니 양지 밑반찬 인근 희모 선택 우려 수육 대추
1
제생 주차장 부근 방문 물냉면 초등학교 포크 응암 응암동 대표 숙성 출구 특선 호선 전문점 뒤편 매우 은평구 음식 수제 맛집 가능 응암역 그린 비빔냉면 이용 점심 메뉴 소갈비 전통 갈비 매장 건물 지하철 대중교통 쌈밥 협소하
2
영동 잠원동 서초 깍두기 서초영 설렁탕 고수 가지 신사역 신사동 호선 김치 허름 음식 운영 식당 겉절이 자랑거리 간장게장 국밥 골목 메뉴 한자리 건너편 역시 수육 외관 집의
3
튀김 한식 메뉴 전통 추천 대표 맛집 신당동 복림 서울 서울특별시 브랜드 중구 전문점 떡볶이 음식
4
케익 태극 학교 분위기 설립 활동 이름 대표 데이트 추억 협회 동참 모나카 카스테라 베이커리 대한민국 민족 제과 음식 자태 광복 이란 창업 이상 서울 역사 발전 사라다 또한 빵집 가장 옛날 우리 제과제빵 먼저 메뉴 고풍 버터 야채 위해 체인점
5
경복궁역 토속 호두 대통령 재료 마늘 산배 계승 생강 노무현 시내 대표 사용 들깨 해바라기씨 검정 음식 더욱 해물파전 맛집 소문 사람 서울 오골계 발전 인삼 종로 유명 양근 전통 율무 신토 삼계탕 정도 호박 위치 대추 토종닭
6
지로 미쉐린 불고기 어르신 대표 시작 가족 선정 부담 전문점 음식 도전 초심자 달리 맛집 냉면 을지로 가이드 다른 메뉴 약간 위치 평양
7
경복궁역 가로수 삼청동 연중 수제비 찹쌀 볶음 일본인 한아름 낙엽 심심찮 때로는 감자전 지나 음식점 수도권 호선 하차 음식 계절 일본 맛집 서울 경복궁 더위 옹심이 종로 색깔 가장 삼청터널 소개 제비집 먼저 새알 잡지 길이 공관 파전 국무총리 건물 호박 지하철 쭈꾸미 벽돌
8
와이키키 캠핑 야외 테이블 한강 모양 크보 수상 도심 감성 한우 데이트 소고기 구독 숯불 가족 웨이 야경 안성맞춤 파라솔 음식 이색 좌석 공원 바베

In [16]:
len(tag_list_city_food), len(tag_list_city)

(5883, 4634)

In [84]:
[' '.join(okt.nouns(f'{question}'))]

['국밥 서초 국밥 서초 설렁탕 서초 수육 서초영 설렁탕 영동 설렁탕 음식 여 년 한자리']

In [165]:
#test 부분
# vectorizer_spot.fit(tag_list_all)

area = '대전'
question = '국밥 힐링'

df_s = spot_df[spot_df['city']== f'{area}']
df_f = food_df[food_df['city'] == f'{area}']

question_tfidf_s = vectorizer_spot.transform([' '.join(okt.nouns(f'{question}'))])
question_tfidf_f = vectorizer_food.transform([' '.join(okt.nouns(f'{question}'))])

cos_similarities_s = linear_kernel(question_tfidf_s, city_matrices_spot[f'{area}'])
cos_similarities_f = linear_kernel(question_tfidf_f, city_matrices_food[f'{area}'])

sorted_indices_s = np.argsort(cos_similarities_s[0])[::-1][:5]
sorted_indices_f = np.argsort(cos_similarities_f[0])[::-1][:5]


# 식당인 것, 아닌 

index_s = sorted_indices_s[0]
index_f = sorted_indices_f[0]

print(len(cos_similarities_s[0]), len(df_s))
print(len(cos_similarities_f[0]), len(df_f))


s = sorted_indices_s[0]
print('spot result')
print(str(df_s.iloc[s]['city']))
print(str(df_s.iloc[s]['title']))
print(float(cos_similarities_s[0][s]))
print(str(df_s.iloc[s]['catchtitle']))
print("---------")
f = sorted_indices_f[0]
print('food result')
print(str(df_f.iloc[f]['city']))
print(str(df_f.iloc[f]['title']))
print(float(cos_similarities_f[0][f]))
print(str(df_f.iloc[f]['catchtitle']))


86 86
187 187
spot result
대전
보문산 전망대
0.08048244069420933

---------
food result
대전
태평소국밥
0.19306831791629644



array([[0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.46684973, 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.36703804],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ],
       [0.        , 0.        , 0.        , ..., 0.        , 0.        ,
        0.        ]])

In [137]:
spot_df[spot_df['title'] == '가덕도대항인공동굴']

id city  cityCode  contentType      title      catchtitle  \
1805   2789460   부산         6           12  가덕도대항인공동굴  아픈 역사를 딛고 아름답게   
12322  2789460   전체         6           12  가덕도대항인공동굴  아픈 역사를 딛고 아름답게   

                                                overView treatMenu  conLike  \
1805   2차 세계대전 말에 일본군은 전력이 급강하하자 부산과 주변 해안에 미군 상륙작전을 ...                  0   
12322  2차 세계대전 말에 일본군은 전력이 급강하하자 부산과 주변 해안에 미군 상륙작전을 ...                  0   

       conRead  ...                 addr                     info parking  \
1805      1129  ...  부산광역시 강서구 대항동 393-9  강서구청 문화체육과 051-970-4062      있음   
12322     1129  ...  부산광역시 강서구 대항동 393-9  강서구청 문화체육과 051-970-4062      있음   

             useTime                                            tagName  \
1805   10:00 ~ 20:00  가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산대항항,부산인공동굴,부산해...   
12322  10:00 ~ 20:00  가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산대항항,부산인공동굴,부산해...   

                             detail         lat       lon  \
1805   입점브랜드:수산물, 채소, 과일, 식육, 잡화 등   128.827469  35.01331   
12322  입점브랜드:수산물, 채소, 과일, 식육, 잡화 등   128.827469  35.01331   

                                                     vec  \
1805   아픈 역사를 딛고 아름답게가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산...   
12322  아픈 역사를 딛고 아름답게가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산...   

                                                   vec_f  
1805   아픈 역사를 딛고 아름답게가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산...  
12322  아픈 역사를 딛고 아름답게가덕도가볼만한곳,가덕도대항인공동굴,관광지,대항인공동굴,부산...  

[2 rows x 22 columns]

In [136]:
food_df[food_df['title'] == '가덕도대항인공동굴']

Empty DataFrame
Columns: [id, city, cityCode, contentType, title, catchtitle, overView, treatMenu, conLike, conRead, conShare, imgPath, addr, info, parking, useTime, tagName, detail, lat, lon, vec, vec_f]
Index: []

[0 rows x 22 columns]

In [114]:
len(df_s)

156

In [112]:
len(cos_similarities_f[0])

156

In [66]:
vectorizer_spot.vocabulary_.items()

dict_items([('설치', 8468), ('기도', 2262), ('활용', 18101), ('여행지', 10708), ('환경', 18063), ('파크', 16517), ('최초', 15530), ('영국', 10911), ('아이', 9990), ('뉴욕', 3135), ('연중', 10831), ('대표', 3648), ('여행', 10701), ('공간', 1230), ('문화', 5544), ('사냥터', 7408), ('데이트', 3759), ('이전', 12622), ('경마장', 759), ('생태관광', 8097), ('관광지', 1395), ('휴식', 18328), ('수원지', 9104), ('연인', 10816), ('상수', 7927), ('대규모', 3442), ('이드', 12497), ('임금', 12910), ('골프장', 1163), ('서울숲', 8200), ('서울', 8197), ('녹색', 3025), ('가족', 149), ('센트럴', 8666), ('수도권', 8989), ('피크닉', 17029), ('관광', 1386), ('이후', 12678), ('테마', 16230), ('현재', 17688), ('코스', 15944), ('규모', 2013), ('한국', 17202), ('반려동물', 5963), ('공원', 1297), ('개원', 491), ('탈바꿈', 16095), ('길상사', 2382), ('중턱', 14486), ('종교', 14169), ('역사', 10719), ('산사', 7659), ('시주', 9529), ('원각', 11822), ('당시', 3387), ('자연환경', 13067), ('사찰', 7554), ('상화', 7999), ('김영한', 2448), ('성북동', 8534), ('체험', 15391), ('위치', 12035), ('불도', 7124), ('불교', 7110), ('예전', 11065), ('주인', 14318), ('비롯', 7242), ('

In [169]:
# 저장
with open('travel_model_v4.pkl', 'wb') as file:
        pickle.dump({"spot":{
                "vectorizer": vectorizer_spot,
                "matrix": matrix_spot,
                "city_matrices": city_matrices_spot
        },"food":{
                "vectorizer": vectorizer_food,
                "matrix": matrix_food,
                "city_matrices": city_matrices_food
        }}, file)

In [26]:
# 불러오기
with open('./travel_model_v3.pkl', 'rb') as file:
    loaded_data = pickle.load(file)
    
    vectorizer_spot = loaded_data["spot"]["vectorizer"]
    matrix_spot = loaded_data["spot"]["matrix"]
    city_matrices_spot = loaded_data["spot"]["city_matrices"]

    vectorizer_food = loaded_data["food"]["vectorizer"]
    matrix_food = loaded_data["food"]["matrix"]
    city_matrices_food = loaded_data["food"]["city_matrices"]

In [ ]:
area = '인천'
question = '캠핑'

df = spot_df[spot_df['city']== f'{area}']

question_tfidf = vectorizer_spot.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_spot[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1][:5]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]



print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



In [15]:
okt = Okt()
a = "샥스핀, 식사류해삼류,단품 요리 바닷가재 등  짬뽕 등  등"
b = "샥스핀, 해삼류, 바닷가재 등 단품 요리, 짜장면, 짬뽕 등 식사류 등"
A = [i for i in okt.morphs(a) if len(i) >1]
B = [i for i in okt.morphs(b) if len(i) >1]
vectorizer = TfidfVectorizer()
text = vectorizer_spot.transform(A)

cosine_similarities = cosine_similarity(text, matrix_spot)
cosine_similarities[0]

print(random.sample(A, len(A)))

['요리', '식사', '샥스핀', '짬뽕', '해삼류', '바닷가재']


In [38]:
len(spot_df), len(food_df), len(df3)

(9268, 11766, 21034)

In [82]:
tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in spot_df['tagName'].tolist()[:2]]
tag_list

['가족 여행 걷기길 관광지 데이트 코스 반려동물 여행지 생태관광 서울숲 수도권 수도권 반려동물 여행지 아이 함께 연인 함께 연중 피크닉 한국 관광 100 휴식 공간 휴식 여행 휴식 하기 휴식 하기 좋은',
 '관광지 길상사 서울 ), 불교 불교 문화 사찰 사찰 여행 산사 수도권 역사 연중 연속 으로 자연 좋은 자연환경 전통 사찰 종교 한국 불교 휴식 공간 휴식 여행 휴식 하기 휴식 하기 좋은']

In [39]:
vectorizer_spot = TfidfVectorizer()

tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in spot_df['tagName'].tolist()]
matrix_spot = vectorizer_spot.fit_transform(tag_list)

# 각 지역에 대한 TF-IDF 행렬 계산
city_matrices_spot = {}    
for city in spot_df['city'].unique():
    city_df = spot_df[spot_df['city'] == city]
    city_tag_list = [' '.join([j for j in okt.morphs(i) if len(j) > 1]) for i in city_df['tagName'].tolist()]
    city_matrices_spot[city] = vectorizer_spot.transform(city_tag_list)

In [5]:
vectorizer_food = TfidfVectorizer()

tag_list = [' '.join([j for j in okt.morphs(str(i)) if len(j) > 1]) for i in food_df['tf'].tolist()]
matrix_food = vectorizer_food.fit_transform(tag_list)

# 각 지역에 대한 TF-IDF 행렬 계산
city_matrices_food = {}    
for city in food_df['city'].unique():
    city_df = food_df[food_df['city'] == city]
    city_tag_list = [' '.join([j for j in okt.morphs(str(i)) if len(j) > 1]) for i in city_df['tf'].tolist()]
    city_matrices_food[city] = vectorizer_food.transform(city_tag_list)

In [6]:

# 저장
with open('travel_model_v2.pkl', 'wb') as file:
        pickle.dump({"spot":{
                "vectorizer": vectorizer_spot,
                "matrix": matrix_spot,
                "city_matrices": city_matrices_spot
        },"food":{
                "vectorizer": vectorizer_food,
                "matrix": matrix_food,
                "city_matrices": city_matrices_food
        }}, file)

In [4]:
with open('./travel_model_v2.pkl', 'rb') as file:
    loaded_data = pickle.load(file)
    
    vectorizer_spot = loaded_data["spot"]["vectorizer"]
    matrix_spot = loaded_data["spot"]["matrix"]
    city_matrices_spot = loaded_data["spot"]["city_matrices"]

    vectorizer_food = loaded_data["food"]["vectorizer"]
    matrix_food = loaded_data["food"]["matrix"]
    city_matrices_food = loaded_data["food"]["city_matrices"]

/home/doxg/.pyenv/versions/3.8.18/lib/python3.8/site-packages/sklearn/base.py:313: UserWarning: Trying to unpickle estimator TfidfTransformer from version 1.3.2 when using version 0.22.2.post1. This might lead to breaking code or invalid results. Use at your own risk.
  warnings.warn(
/home/doxg/.pyenv/versions/3.8.18/lib/python3.8/site-packages/sklearn/base.py:313: UserWarning: Trying to unpickle estimator TfidfVectorizer from version 1.3.2 when using version 0.22.2.post1. This might lead to breaking code or invalid results. Use at your own risk.
  warnings.warn(


In [ ]:
#     # 미리 계산된 해당 지역의 TF-IDF 행렬 사용
# if question.area == '전체':
#     city_tfidf_matrix = tfidf_matrix
# else:
#     city_tfidf_matrix = city_tfidf_matrices.get(question.area)
#     df = df[df['city']== f'{question.area}']

In [35]:
city_matrices_spot['충남']

<351x5323 sparse matrix of type '<class 'numpy.float64'>'
	with 5212 stored elements in Compressed Sparse Row format>

In [74]:
city_matrices_spot['인천']

<5995x18425 sparse matrix of type '<class 'numpy.float64'>'
	with 5995 stored elements in Compressed Sparse Row format>

In [90]:
area = '인천'
question = '캠핑'

df = spot_df[spot_df['city']== f'{area}']

question_tfidf = vectorizer_spot.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_spot[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]
print(index)


print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



NotFittedError: The TF-IDF vectorizer is not fitted

In [70]:
area = '대구'
question = '피자'

df = food_df[food_df['city']== f'{area}']

question_tfidf = vectorizer_food.transform(okt.morphs(f'{question}'))

cos_similarities = cosine_similarity(question_tfidf, city_matrices_food[f'{area}'])
sorted_indices = np.argsort(cos_similarities[0])[::-1][:5]
print('indices= ',len(sorted_indices))
print('df= ', len(df))
# 식당인 것, 아닌 

index = sorted_indices[0]



print(
str(df.iloc[index]['id']),
str(df.iloc[index]['city']),
str(df.iloc[index]['title']),
float(cos_similarities[0][index]),
str(df.iloc[index]['catchtitle']))



indices=  5
df=  192
2866244 대구 루미너스 0.42204924949455175 모던한 분위기의 한우 안심 스테이크 맛집


In [14]:
np.argsort(cos_similarities[0])[::-1][0]

63

In [15]:
cos_similarities[0][63]

0.30805653331899097

In [27]:
df = pd.read_csv('./travel_spot_v1.csv', index_col=0)

In [29]:
okt = Okt()

In [35]:
question_area = '인천'
question_question = '효도여행'

# 미리 계산된 해당 지역의 TF-IDF 행렬 사용
if question_area == '전체':
    city_tfidf_matrix = tfidf_matrix
else:
    city_tfidf_matrix = city_tfidf_matrices.get(question_area)
    df = df[df['city']== f'{question_area}']

print('여기여기')

if city_tfidf_matrix is None:
    print(JSONResponse(content={"error": f"No data found for city: {question_area}"}, status_code=404))

# 질문과 선택된 지역의 TF-IDF로 유사도 계산
question_tfidf = tfidf_vectorizer.transform(okt.morphs(question_question))
cos_similarities = cosine_similarity(question_tfidf, city_tfidf_matrix)
sorted_indices = np.argsort(cos_similarities[0])[::-1]
len(sorted_indices)

여기여기


352

In [81]:
restaurant = sorted_indices[df.iloc[sorted_indices]['contentType'].eq(39)].tolist()[:5]
non_restaurant = sorted_indices[~df.iloc[sorted_indices]['contentType'].eq(39)].tolist()[:5]

restaurant,non_restaurant

([111, 112, 113, 114, 115], [351, 350, 296, 288, 289])

In [62]:
len(df), len(sorted_indices)

(352, 352)

In [60]:
len(sorted_indices)

352

In [52]:

print('여기여기2')

from itertools import islice
# 식당인 것, 아닌 것
restaurant = islice((index for index in sorted_indices if df.iloc[index]['contentType'] == 39 ), 5)
non_restaurant = islice((index for index in sorted_indices if df.iloc[index]['contentType'] != 39 ), 5)

list(restaurant), list(non_restaurant)

여기여기2


([111, 112, 113, 114, 115], [351, 350, 296, 288, 289])

In [51]:
str(df.iloc[111]['city'])

'인천'

In [55]:
str(df.iloc[111]['id'])

'2758144'

In [53]:
def add_to_similar_tags(sorted_indices,similar_tags):
    bag = []
    for index in sorted_indices:
        print("Current index:", index)
        bag.append({
            "id": str(df.iloc[index]['id']),
            "area": str(df.iloc[index]['city'])})
        similar_tags.append(bag)

In [78]:
restaurant


In [57]:

# 결과를 저장할 리스트 초기화
similar_tags = []
print('여기여기 3')
# 리스트로 추가
def add_to_similar_tags(sorted_indices,similar_tags):
    bag = []
    for index in sorted_indices:
        print("Current index:", index)
        bag.append({
            "id": str(df.iloc[index]['id']),
            "area": str(df.iloc[index]['city']),
            "title": str(df.iloc[index]['title']),
            "similarity": float(cos_similarities[0][index]),
            "catchtitle": str(df.iloc[index]['catchtitle']),
            # "detail": str(df.iloc[index]['detail']),
            "treatMenu": str(df.iloc[index]['treatMenu']),
            "tagName": str(df.iloc[index]['tagName']),
            "addr": str(df.iloc[index]['addr']),
            "info": str(df.iloc[index]['info']),
            # "lat": str(df.iloc[index]['parking']),
            "useTime": str(df.iloc[index]['useTime']),
            "conLike": str(df.iloc[index]['conLike']),
            "conRead": str(df.iloc[index]['conRead']),
            "conShare": str(df.iloc[index]['conShare']),
            # "overView": str(df.iloc[index]['overView']),
            "lat": str(df.iloc[index]['lat']),
            "lon": str(df.iloc[index]['lon'])
            
            })
    similar_tags.append(bag)
print('여기여기4')

# 함수를 사용
add_to_similar_tags(non_restaurant,similar_tags)
add_to_similar_tags(restaurant,similar_tags)
similar_tags

여기여기 3
여기여기4


[[], []]

In [76]:
sorted_indices.__len__()

352

In [73]:
# 결과를 저장할 리스트 초기화
similar_tags = []

def add_to_similar_tags(sorted_indices):
    bag = []
    sorted_indices = list(sorted_indices)[:len(df)]
    print("sorted_indices length:", len(sorted_indices))
    for index in sorted_indices:
        print("Processing index:", index)
        if 0 <= index < len(df):
            print("Adding to bag:", index)
            bag.append({
                "id": str(df.iloc[index]['id']),
                "area": str(df.iloc[index]['city']),
                "title": str(df.iloc[index]['title']),
                "similarity": float(cos_similarities[0][index]),
                "catchtitle": str(df.iloc[index]['catchtitle']),
                "treatMenu": str(df.iloc[index]['treatMenu']),
                "tagName": str(df.iloc[index]['tagName']),
                "addr": str(df.iloc[index]['addr']),
                "info": str(df.iloc[index]['info']),
                "useTime": str(df.iloc[index]['useTime']),
                "conLike": str(df.iloc[index]['conLike']),
                "conRead": str(df.iloc[index]['conRead']),
                "conShare": str(df.iloc[index]['conShare']),
                "lat": str(df.iloc[index]['lat']),
                "lon": str(df.iloc[index]['lon'])
            })
        else:
            print("Index out of bounds:", index)
    print("Adding bag to similar_tags:", bag)
    similar_tags.append(bag)

# 함수를 사용
add_to_similar_tags(non_restaurant)
add_to_similar_tags(restaurant)

print("Final similar_tags:", similar_tags)


sorted_indices length: 0
Adding bag to similar_tags: []
sorted_indices length: 0
Adding bag to similar_tags: []
Final similar_tags: [[], []]
